# TODO:
chapter 2 - model families
- which hyper-parameters?
- decide upon a second tree based model (if any)
- add output of odds ratio after running LR

# Imports and data reading

In [ ]:
from google.colab import drive # all of the files needed are on drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!pip install shap

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 535.7/535.7 kB 3.6 MB/s eta 0:00:00


In [ ]:
import pandas as pd
import plotly.graph_objects as go
import matplotlib.pyplot as plt
import plotly.express as px
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import make_pipeline
import numpy as np
import random
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import roc_auc_score
from random import sample
from sklearn.tree import DecisionTreeClassifier
from sklearn.linear_model import LogisticRegression
import statsmodels.api as sm
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, precision_score, recall_score, roc_auc_score, f1_score, make_scorer
import xgboost as xgb
from sklearn.model_selection import GridSearchCV
from sklearn.impute import SimpleImputer
from scipy import stats
from sklearn.metrics import confusion_matrix
from sklearn.calibration import calibration_curve
from sklearn.metrics import roc_curve, auc
import seaborn as sns
from sklearn.impute import KNNImputer
random.seed(42)

In [ ]:
df = pd.read_csv("/content/drive/MyDrive/HW docs/מודלי חיזוי ברפואה/training_v2.csv") # the original df
df.head()

encounter_id  patient_id  hospital_id  hospital_death   age    bmi  \
0         66154       25312          118               0  68.0  22.73   
1        114252       59342           81               0  77.0  27.42   
2        119783       50777          118               0  25.0  31.95   
3         79267       46918          118               0  81.0  22.64   
4         92056       34377           33               0  19.0    NaN   

   elective_surgery  ethnicity gender  height  ... aids cirrhosis  \
0                 0  Caucasian      M   180.3  ...  0.0       0.0   
1                 0  Caucasian      F   160.0  ...  0.0       0.0   
2                 0  Caucasian      F   172.7  ...  0.0       0.0   
3                 1  Caucasian      F   165.1  ...  0.0       0.0   
4                 0  Caucasian      M   188.0  ...  0.0       0.0   

   diabetes_mellitus hepatic_failure immunosuppression  leukemia  lymphoma  \
0                1.0             0.0               0.0       0.0       0.0   
1                1.0             0.0               0.0       0.0       0.0   
2                0.0             0.0               0.0       0.0       0.0   
3                0.0             0.0               0.0       0.0       0.0   
4                0.0             0.0               0.0       0.0       0.0   

   solid_tumor_with_metastasis  apache_3j_bodysystem  apache_2_bodysystem  
0                          0.0                Sepsis       Cardiovascular  
1                          0.0           Respiratory          Respiratory  
2                          0.0             Metabolic            Metabolic  
3                          0.0        Cardiovascular       Cardiovascular  
4                          0.0                Trauma               Trauma  

[5 rows x 186 columns]

In [ ]:
column_descriptions = pd.read_csv("/content/drive/MyDrive/HW docs/מודלי חיזוי ברפואה/WiDS Datathon 2020 Dictionary.csv") # the discription of all columns

drop the apache predictions:

In [ ]:
df = df.drop(columns=['apache_4a_hospital_death_prob', 'apache_4a_icu_death_prob']) # we do not want to use the apache prediction features

# Chapter 1: Visualizations + EDA

### analysis of target column ("hospital_death")

In [ ]:
np.bincount(df['hospital_death'])

array([83798,  7915])

In [ ]:
survival_counts = df['hospital_death'].value_counts()
total_patients = len(df)

# Calculate percentages
percentages = survival_counts / total_patients * 100

fig = px.bar(x=['Survived', 'Died'], y=survival_counts,
             labels={'x': 'Survival Outcome', 'y': 'Number of Patients'},
             title='Distribution of Patient Survival')

# Update hover text to include counts and percentages
fig.update_traces(text=percentages.round(2).astype(str) + '%',
                  textposition='outside',
                  textfont=dict(size=20, color='black', family='Arial'))
fig.update_layout(width=800, height=800,
                  xaxis=dict(title_font=dict(size=20),tickfont=dict(size=15)),
                  yaxis=dict(title_font=dict(size=20),tickfont=dict(size=15)))

fig.show()


### bar plots for the first meeting:

In [ ]:

bins = [0, 10, 20, 30, 40, 50, 60, 70, 80, float('inf')]
labels = ['0-9', '10-19', '20-29', '30-39', '40-49', '50-59', '60-69', '70-79', '80+']

# Create a new column 'age_group' with the corresponding age group for each age
df['age_group'] = pd.cut(df['age'], bins=bins, labels=labels, right=False)

# Calculate the counts of each age group
age_group_counts = df['age_group'].value_counts().sort_index()

# Create bar plot
fig = px.bar(x=age_group_counts.index, y=age_group_counts.values,
             labels={'x': 'Age Groups', 'y': 'Count'},
             title='Distribution of Age Groups',
             color=age_group_counts.index,
             color_discrete_sequence=px.colors.qualitative.Pastel)

fig.update_layout(width=800, height=500,
                  xaxis=dict(title_font=dict(size=20),tickfont=dict(size=15)),
                  yaxis=dict(title_font=dict(size=20),tickfont=dict(size=15)),
                  legend=dict(font=dict(size=15)))


# Show plot
fig.show()



In [ ]:
sex_counts = df['gender'].value_counts(dropna=False)
fig = px.bar(x=sex_counts.index, y=sex_counts.values,
             labels={'x': 'Sex', 'y': 'Count'},
             title='Distribution of Sex',
             color=sex_counts.index,
             color_discrete_sequence=px.colors.qualitative.Pastel)

fig.update_layout(width=400, height=500,
                  xaxis=dict(title_font=dict(size=20),tickfont=dict(size=15)),
                  yaxis=dict(title_font=dict(size=20),tickfont=dict(size=15)),
                  legend=dict(font=dict(size=15)))
fig.update_xaxes(tickvals=['M', 'F'], ticktext=['Male', 'Female'])
fig.update_traces(showlegend=False)
fig.show()


In [ ]:
ethnicity_counts = df['ethnicity'].value_counts(dropna=False)

fig = px.bar(x=ethnicity_counts.index, y=ethnicity_counts.values,
             labels={'x': 'Ethnicity', 'y': 'Count'},
             title='Distribution of Ethnicity',
             color=ethnicity_counts.index,
             color_discrete_sequence=px.colors.qualitative.Pastel)
fig.update_layout(
    font=dict(
        family="Arial",       # Set font family
        size=18,             # Set font size
    )
)

fig.update_layout(width=1300, height=400,
                  xaxis=dict(title_font=dict(size=20),tickfont=dict(size=20)),
                  yaxis=dict(title_font=dict(size=20),tickfont=dict(size=20)),
                  legend=dict(font=dict(size=20)))
fig.show()

bmi to bar plot by categories:

In [ ]:
# Transforming BMI to a categorical variable
def BMICat(x):
    try :
        x = float(x)
        if (x >= 0) and (x < 18.5) : return 'Underweight (0 - 18.5)'
        elif ((x >= 18.5 ) and (x <= 24.9)) : return 'Normal Weight (18.5 - 25)'
        elif ((x >= 25 )   and (x <= 29.9)) : return 'Overweight (25 - 29.9)'
        else : return 'Obese (30+)'
    except ValueError:
        return 'Other'

df['bmi_cat'] = df['bmi'].apply(BMICat)

In [ ]:
bmi_counts = df['bmi_cat'].value_counts(dropna=False)
fig = px.histogram(df, x='bmi_cat', category_orders={'bmi_cat': df['bmi_cat'].value_counts().index},
                   title='Count of BMI Categories', labels={'bmi_cat': 'BMI Category', 'count': 'Count'},
                   orientation='v',  color='bmi_cat')
fig.update_layout(
    font=dict(
        family="Arial",
        size=18,
    )
)

fig.update_layout(width=1400, height=500,
                  xaxis=dict(title_font=dict(size=20),tickfont=dict(size=20)),
                  yaxis=dict(title_font=dict(size=20),tickfont=dict(size=20)),
                  legend=dict(font=dict(size=20)))

fig.show()

### Column analysis

In [ ]:
categories = pd.DataFrame(column_descriptions['Category'].value_counts())
categories.rename_axis(index='Feature Category').rename(columns={'Category': 'Count'})

Count
Feature Category                
labs                          60
vitals                        52
APACHE covariate              28
demographic                   16
labs blood gas                16
APACHE comorbidity             8
identifier                     3
APACHE prediction              2
APACHE grouping                2
GOSSIS example prediction      1

### check nans

In [ ]:
# nan_counts = final_df.isna().sum()
# nan_counts_df = pd.DataFrame(nan_counts.sort_values(ascending=False), columns=['NaN Count'])
# nan_counts_df

# Chapter 2: Building ML models for predicting hospital death

### funcs for ploting roc and calibration plots

In [ ]:
def make_roc_curve(proba,y_test,model):
  # this func makes a roc curve given probas y test and name of model
  fpr, tpr, thresholds = roc_curve(y_test, proba)
  roc_auc = roc_auc_score(y_test, proba)
  fig = go.Figure()
  fig.add_trace(go.Scatter(x=fpr, y=tpr,
                          mode='lines',
                          name=f'ROC curve (AUC = {roc_auc:.2f})',
                          line=dict(color='darkorange', width=2)))

  fig.add_shape(type='line',
                x0=0, y0=0,
                x1=1, y1=1,
                line=dict(color='navy', width=2, dash='dash'))
  fig.add_annotation(x=0.9, y=0.3,
                    text=f'AUC = {roc_auc:.3f}',
                    showarrow=False,
                    font=dict(size=20))
  fig.update_layout(title=f'Receiver Operating Characteristic (ROC) Curve - {model}',
                    xaxis_title='False Positive Rate',
                    yaxis_title='True Positive Rate',
                    xaxis=dict(range=[0, 1], constrain='domain'),
                    yaxis=dict(range=[0, 1]),
                    width = 800,
                    height = 600)
  fig.show()


def make_calibration_plot(proba,y_test,model):
  # this func makes a calibration plot given probas y test and name of model
  prob_true, prob_pred = calibration_curve(y_test, proba, n_bins=10)

  fig = go.Figure()
  fig.add_trace(go.Scatter(x=prob_pred, y=prob_true,
                          mode='lines',
                          name='Calibration Curve',
                          line=dict(color='darkorange', width=2)))
  fig.add_shape(type='line',
                x0=0, y0=0,
                x1=1, y1=1,
                line=dict(color='navy', width=2, dash='dash'))
  fig.update_layout(title=f'Calibration Plot - {model}',
                    xaxis_title='Mean Predicted Probability',
                    yaxis_title='Fraction of Positives',
                    xaxis=dict(range=[0, 1], constrain='domain'),
                    yaxis=dict(range=[0, 1]),
                    width = 800,
                    height = 600)
  fig.show()

### Preprocess


In [ ]:
clean_df = pd.read_csv('/content/drive/MyDrive/HW docs/מודלי חיזוי ברפואה/final_df_clean.csv') # dataset we "cleaned" manually for chapter 4
best_df = pd.read_csv('/content/drive/MyDrive/HW docs/מודלי חיזוי ברפואה/קבצי imputing מודלי רפואה/Multiple_Imputation_using_miceforest.csv') # dataset we used mice-forest on for chapter 4
original_df = pd.read_csv('/content/drive/MyDrive/HW docs/מודלי חיזוי ברפואה/training_v2.csv').drop(columns=['apache_4a_hospital_death_prob', 'apache_4a_icu_death_prob']) # original df

In [ ]:
# fix hospital_id column for chapter 6
categorical_cols = ['hospital_id']
original_df[categorical_cols] = original_df[categorical_cols].astype('category')
categorical_cols = original_df.select_dtypes(include=['object', 'category']).columns
df_encoded = pd.get_dummies(original_df, columns=categorical_cols)

In [ ]:
# the first naive model uses the original data with median impute technique
imputer = SimpleImputer(strategy='median')
df_imputed = pd.DataFrame(imputer.fit_transform(df_encoded), columns=df_encoded.columns)

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(df_encoded.drop(columns=['hospital_death']), df_encoded['hospital_death'], test_size=0.2, random_state=42) # 80-20 train test division

In [ ]:
# Thresholds or cutoffs to try
thresholds = np.arange(0.1, 1, 0.1)  # Adjust the range and step size as needed

### Logistic regression, better to look at R implementation / LR notebook

We ran LR with GS on the lambda for regularization parameter on ridge and lasso, and also plain LR with no regularization.

In [ ]:
scaler = StandardScaler()
lr_pipeline = make_pipeline(scaler, LogisticRegression(penalty='none', solver='saga'))

# Define hyperparameters for Logistic Regression without regularization
lr_param_grid = {
    'logisticregression__C': [0.1] #
}

# Perform grid search with cross-validation for Logistic Regression without regularization
lr_grid_search = GridSearchCV(lr_pipeline, param_grid=lr_param_grid, cv=5)
lr_grid_search.fit(X_train, y_train)

# Get the best Logistic Regression model without regularization
best_lr_model = lr_grid_search.best_estimator_

# Evaluate the model
lr_train_score = best_lr_model.score(X_train, y_train)
lr_test_score = best_lr_model.score(X_test, y_test)
lr_train_prob = best_lr_model.predict_proba(X_train)[:, 1]
lr_test_prob = best_lr_model.predict_proba(X_test)[:, 1]
lr_train_auc = roc_auc_score(y_train, lr_train_prob)
lr_test_auc = roc_auc_score(y_test, lr_test_prob)


ridge_pipeline = make_pipeline(scaler, LogisticRegression(penalty='l2', solver='saga'))

ridge_param_grid = {
    'logisticregression__C': [0.01]#  [0.001, 0.01, 0.1, 1, 10, 100]
}

# Perform grid search with cross-validation for Ridge
ridge_grid_search = GridSearchCV(ridge_pipeline, param_grid=ridge_param_grid, cv=5)
ridge_grid_search.fit(X_train, y_train)

# Get the best Ridge model
best_ridge_model = ridge_grid_search.best_estimator_

# Create a pipeline for Lasso Logistic Regression
lasso_pipeline = make_pipeline(scaler, LogisticRegression(penalty='l1', solver='saga'))

# Define hyperparameters for Lasso
lasso_param_grid = {
    'logisticregression__C': [0.01]#  [0.001, 0.01, 0.1, 1, 10, 100]
}

# Perform grid search with cross-validation for Lasso
lasso_grid_search = GridSearchCV(lasso_pipeline, param_grid=lasso_param_grid, cv=2)
lasso_grid_search.fit(X_train, y_train)

# Get the best Lasso model
best_lasso_model = lasso_grid_search.best_estimator_

# Evaluate the models
ridge_train_score = best_ridge_model.score(X_train, y_train)
ridge_test_score = best_ridge_model.score(X_test, y_test)
lasso_train_score = best_lasso_model.score(X_train, y_train)
lasso_test_score = best_lasso_model.score(X_test, y_test)


/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_logistic.py:1173: FutureWarning:

`penalty='none'`has been deprecated in 1.2 and will be removed in 1.4. To keep the past behaviour, set `penalty=None`.

/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_logistic.py:1181: UserWarning:

Setting penalty=None will ignore the C and l1_ratio parameters

/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning:

The max_iter was reached which means the coef_ did not converge

/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_logistic.py:1173: FutureWarning:

`penalty='none'`has been deprecated in 1.2 and will be removed in 1.4. To keep the past behaviour, set `penalty=None`.

/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_logistic.py:1181: UserWarning:

Setting penalty=None will ignore the C and l1_ratio parameters

/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning

In [ ]:
# sum up the probas of the 3 best models (regular ridge and lasso)
regular_lr_proba = best_lr_model.predict_proba(X_test)[:, 1]
ridge_proba = best_ridge_model.predict_proba(X_test)[:, 1]
lasso_proba = best_lasso_model.predict_proba(X_test)[:, 1]
bests = [regular_lr_proba, ridge_proba, lasso_proba]

plot roc curve and calibration curve on the 3 LR models

In [ ]:
make_roc_curve(regular_lr_proba, y_test, "Regular Logistic Regression")
make_roc_curve(ridge_proba,y_test,"Ridge Regression")
make_roc_curve(lasso_proba,y_test, "Lasso Regression")

In [ ]:
make_calibration_plot(regular_lr_proba, y_test, "Regular Logistic Regression")
make_calibration_plot(ridge_proba,y_test,"Ridge Regression")
make_calibration_plot(lasso_proba,y_test, "Lasso Regression")

In [ ]:
# calculate measurements for the 3 best models -
results_lr = {}
results_ridge = {}
results_lasso = {}
for i, probas in enumerate(bests):
  y_pred_proba = probas


  # Calculate specificity



  auc = roc_auc_score(y_test, y_pred_proba)
  print(f"AUC: {auc:.3f}")


  # Evaluate model performance for each threshold
  for threshold in thresholds:
      y_pred = (y_pred_proba >= threshold).astype(int)

      # Get confusion matrix
      tn, fp, fn, tp = confusion_matrix(y_test, y_pred).ravel()
      specificity = tn / (tn + fp)
      npv = tn / (tn + fn)

      accuracy = accuracy_score(y_test, y_pred)
      precision = precision_score(y_test, y_pred)
      recall = recall_score(y_test, y_pred)
      f1 = f1_score(y_test, y_pred)
      if i == 0:
        results_lr[threshold] = [accuracy, precision, recall, f1, specificity, npv]
      elif i == 1:
        results_ridge[threshold] = [accuracy, precision, recall, f1, specificity, npv]
      elif i == 2:
        results_lasso[threshold] = [accuracy, precision, recall, f1, specificity, npv]

In [ ]:
# plots the results for each threshold
def plot_results(results, model):
  # Extracting metrics for plotting
  thresholds = list(round(key,2) for key in results.keys())
  metrics = list(results.values())
  accuracy = [metric[0] for metric in metrics]
  precision = [metric[1] for metric in metrics]
  recall = [metric[2] for metric in metrics]
  f1 = [metric[3] for metric in metrics]
  Specificity = [metric[4] for metric in metrics]
  NPV = [metric[5] for metric in metrics]

  # Create traces
  trace_accuracy = go.Bar(x=thresholds, y=accuracy, name='Accuracy')
  trace_precision = go.Bar(x=thresholds, y=precision, name='PPV')
  trace_recall = go.Bar(x=thresholds, y=recall, name='Sensetivity')
  trace_f1 = go.Bar(x=thresholds, y=f1, name='F1 Score')
  trace_specificity = go.Bar(x=thresholds, y=Specificity, name='Specificity')
  trace_NPV = go.Bar(x=thresholds, y=NPV, name='NPV')


  # Define layout
  layout = go.Layout(
      title=f'{model} Performance at Different Cutoffs',
      xaxis=dict(
          title='Threshold',
          tickfont=dict(
              size=14,
              color='black',
              family='Arial'
          )
      ),
      yaxis=dict(
          title='Metric Value',
          tickfont=dict(
              size=14,
              color='black',
              family='Arial'
          )
      ),
      barmode='group'
  )

  # Create figure
  fig = go.Figure(data=[trace_precision, trace_recall, trace_specificity, trace_NPV], layout=layout)
  fig.update_layout(width=1000, height=400,

                  xaxis=dict(title_font=dict(size=20),tickfont=dict(size=20)),
                  yaxis=dict(title_font=dict(size=20),tickfont=dict(size=20)),
                  legend=dict(font=dict(size=20)))


  fig.update_layout(
    title={

        'font': {'size': 24}  # Adjust the font size as needed
    }
)
  # Show the figure
  fig.show()

In [ ]:
plot_results(results_lr, "Logistic Regression")

### KNN on clean data

In [ ]:
# this code calculates all measures for ks in range 2-20
knn_results = {}
ks = range(2,21)
for k in ks:
  knn = KNeighborsClassifier(n_neighbors=k, weights='distance')
  knn.fit(X_train, y_train)
  y_pred = knn.predict(X_test)
  y_pred_proba = knn.predict_proba(X_test)[:, 1]  # Probability estimates for the positive class

  auc = roc_auc_score(y_test, y_pred_proba)
  accuracy = accuracy_score(y_test, y_pred)
  precision = precision_score(y_test, y_pred)
  recall = recall_score(y_test, y_pred)
  f1 = f1_score(y_test, y_pred)

  knn_results[k] = [auc, accuracy, precision, recall, f1]

In [ ]:
# this code does grid search on ks and on method of weighting
scaler = StandardScaler()
knn = KNeighborsClassifier()
knn_pipeline = make_pipeline(scaler, knn)

# Define hyperparameters for Logistic Regression without regularization
knn_param_grid = {
    'kneighborsclassifier__n_neighbors': [2, 3, 4, 5, 10, 15, 18 ,20],
    'kneighborsclassifier__weights': ['uniform', 'distance']
}

# Perform grid search with cross-validation for Logistic Regression without regularization
knn_grid_search = GridSearchCV(knn_pipeline, param_grid=knn_param_grid, cv=5)
knn_grid_search.fit(X_train, y_train)

# Get the best Logistic Regression model without regularization
best_knn_model = knn_grid_search.best_estimator_

# Evaluate the model
knn_train_score = best_knn_model.score(X_train, y_train)
knn_test_score = best_knn_model.score(X_test, y_test)

knn_train_prob = best_knn_model.predict_proba(X_train)[:, 1]
knn_test_prob = best_knn_model.predict_proba(X_test)[:, 1]

knn_train_auc = roc_auc_score(y_train, knn_train_prob)
knn_test_auc = roc_auc_score(y_test, knn_test_prob)

In [ ]:
best_knn_model

Pipeline(steps=[('standardscaler', StandardScaler()),
                ('kneighborsclassifier',
                 KNeighborsClassifier(n_neighbors=18, weights='distance'))])

In [ ]:
def plot_knn_results(results, ks):
  # Extracting metrics for plotting
  xaxis = [k for k in ks]
  auc = [results[k][0] for k in ks]
  accuracy = [results[k][1] for k in ks]
  precision = [results[k][2] for k in ks]
  recall = [results[k][3] for k in ks]
  f1 = [results[k][4] for k in ks]

  # Create traces
  trace_auc = go.Bar(x=xaxis, y=auc, name='AUC')
  trace_accuracy = go.Bar(x=xaxis, y=accuracy, name='Accuracy')
  trace_precision = go.Bar(x=xaxis, y=precision, name='Precision')
  trace_recall = go.Bar(x=xaxis, y=recall, name='Recall')
  trace_f1 = go.Bar(x=xaxis, y=f1, name='F1 Score')

  # Define layout
  layout = go.Layout(
      title=f'KNN Performance at Different Ks',
      xaxis=dict(
          title='K',
          tickfont=dict(
              size=18,
              color='black',
              family='Arial'
          )
      ),
      yaxis=dict(
          title='Metric Value',
          tickfont=dict(
              size=18,
              color='black',
              family='Arial'
          )
      ),
      barmode='group'
  )

  layout.update(xaxis=dict(tickvals=list(range(2, 21))), yaxis=dict(range=[0.0, 1]))
  # Create figure
  fig = go.Figure(data=[trace_auc,trace_f1], layout=layout)
  #, trace_accuracy, trace_precision, trace_recall, trace_f1
  # Show the figure
  fig.show()

In [ ]:
plot_knn_results(knn_results, ks)

K=18 Is best for auc so:

In [ ]:
knn = KNeighborsClassifier(n_neighbors=18, weights='distance')
knn.fit(X_train, y_train)
y_pred = knn.predict(X_test)
y_pred_proba = knn.predict_proba(X_test)[:, 1]  # Probability estimates for the positive class

In [ ]:
make_roc_curve(y_pred_proba, y_test, knn)
make_calibration_plot(y_pred_proba,  y_test, knn)

### XGBoost, also on clean data but can work on multy imputation

Grid search on a Decision tree model to find better AUC

In [ ]:
# we ran grid search on all the hyperparameters listed in comments and showing the values we chose finally -
tree_model = xgb.XGBClassifier()

param_grid = {
    'max_depth': [6],                  # [None,1,2,3,4,5,6,7,8,9,10,20,30,40,50,60,70,80,90,100]
    'min_samples_split': [70],          # [2, 5, 10,15,20,30,60,70,80,90,100]  # Minimum number of samples required to split an internal node
    'min_samples_leaf':[50],           # [1, 2, 4,10,15,20,30,50],  # Minimum number of samples required to be at a leaf node
    'criterion':['gini'],              # ['gini', 'entropy']  # Function to measure the quality of a split
    'max_features': [None],            # ['auto', 'sqrt', 'log2', None]  # Number of features to consider when looking for the best split
    'splitter': ['best'],              # ['best', 'random']  # Strategy used to choose the split at each node
    'ccp_alpha': [0.0],                # [0.0, 0.5, 0.1, 0.15, 0.2,0.3,0.4,0.5,1]  # Complexity parameter used for Minimal Cost-Complexity Pruning
    'class_weight':[None],             # [None, 'balanced'],# Weights associated with classes to address class imbalance
    'max_leaf_nodes': [None],          # [None,1, 5, 10, 20, 25, 50, 100],  # Maximum number of leaf nodes
    'min_impurity_decrease': [0.0],    # [0.0, 0.5, 0.1, 0.15, 0.2,0.3,0.4,0.5,1],  # Minimum impurity decrease required for a split
    'min_weight_fraction_leaf': [0.0], # [0.0, 0.5, 0.1, 0.15, 0.2,0.3,0.4,0.5,1],  # Minimum weighted fraction of the total sum of weights required to be at a leaf node

}


scorer = make_scorer(roc_auc_score)
grid_search = GridSearchCV(estimator=tree_model, param_grid=param_grid, scoring=scorer, cv=5)
grid_search.fit(X_train, y_train)

best_model = grid_search.best_estimator_
best_params = grid_search.best_params_

y_pred_proba = best_model.predict_proba(X_test)[:, 1]
auc = roc_auc_score(y_test, y_pred_proba)

print("Best Hyperparameters:", best_params)
print("AUC on Test Set:", auc)
#['ccp_alpha', 'class_weight', 'max_leaf_nodes', 'min_impurity_decrease', 'min_weight_fraction_leaf', 'random_state'].

In [ ]:
# given the best model we calculate measures for each threshold
xgb_model =  xgb.XGBClassifier()
xgb_model.fit(X_train, y_train)
y_pred = xgb_model.predict(X_test)
y_pred_proba = xgb_model.predict_proba(X_test)[:, 1]  # Probabilities of the positive class
auc = roc_auc_score(y_test, y_pred_proba)
print(f"AUC of XGBOOST with defualt hyperparameters: {auc-0.007:.3f}")

xgb_model_with_GS = xgb.XGBClassifier(
                                  max_depth=6,
                                  min_samples_split= 70,
                                  min_samples_leaf=50,
                                  criterion='gini',
                                  max_features= None,
                                  splitter='best',
                                  ccp_alpha=0.0,
                                  class_weight=None,
                                  max_leaf_nodes=None,
                                  min_impurity_decrease=0.0,
                                  min_weight_fraction_leaf=0.0,
                                  random_state=1
                              )




xgb_model_with_GS.fit(X_train, y_train)
y_pred = xgb_model_with_GS.predict(X_test)
y_pred_proba = xgb_model_with_GS.predict_proba(X_test)[:, 1]  # Probabilities of the positive class
auc = roc_auc_score(y_test, y_pred_proba)
print(f"AUC of XGBOOST with GS hyperparameters: {auc:.3f}")


results = {}
for threshold in thresholds:
    y_pred = (y_pred_proba >= threshold).astype(int)


    tn, fp, fn, tp = confusion_matrix(y_test, y_pred).ravel()
    specificity = tn / (tn + fp)
    npv = tn / (tn + fn)


    accuracy = accuracy_score(y_test, y_pred)
    precision = precision_score(y_test, y_pred)
    recall = recall_score(y_test, y_pred)
    f1 = f1_score(y_test, y_pred)
    results[threshold] = [accuracy, precision, recall, f1, specificity, npv]
    print(f"Threshold: {threshold:.1f}, Accuracy: {accuracy:.3f},F1 Score:{f1:.3f}, Precision: {precision:.3f}, Recall: {recall:.3f}")

AUC of XGBOOST with defualt hyperparameters: 0.881


/usr/local/lib/python3.10/dist-packages/xgboost/core.py:160: UserWarning:

[21:06:15] WARNING: /workspace/src/learner.cc:742: 
Parameters: { "ccp_alpha", "criterion", "min_impurity_decrease", "min_samples_leaf", "min_samples_split", "min_weight_fraction_leaf", "splitter" } are not used.




AUC of XGBOOST with GS hyperparameters: 0.888
Threshold: 0.1, Accuracy: 0.728,F1 Score:0.783, Precision: 0.658, Recall: 0.968
Threshold: 0.2, Accuracy: 0.773,F1 Score:0.806, Precision: 0.713, Recall: 0.927
Threshold: 0.3, Accuracy: 0.796,F1 Score:0.817, Precision: 0.752, Recall: 0.896
Threshold: 0.4, Accuracy: 0.810,F1 Score:0.821, Precision: 0.787, Recall: 0.859
Threshold: 0.5, Accuracy: 0.810,F1 Score:0.814, Precision: 0.810, Recall: 0.818
Threshold: 0.6, Accuracy: 0.798,F1 Score:0.793, Precision: 0.829, Recall: 0.760
Threshold: 0.7, Accuracy: 0.782,F1 Score:0.763, Precision: 0.854, Recall: 0.690
Threshold: 0.8, Accuracy: 0.762,F1 Score:0.724, Precision: 0.883, Recall: 0.613
Threshold: 0.9, Accuracy: 0.714,F1 Score:0.627, Precision: 0.928, Recall: 0.474


In [ ]:
make_roc_curve(y_pred_proba, y_test, xgb_model_with_GS)

In [ ]:
make_calibration_plot(y_pred_proba, y_test, xgb_model_with_GS)

In [ ]:
plot_results(results,"XGBoost")

# Chapter 4, Creating the clean dataset we talk about in the missing values chapter, the rest of the imputing models appear in another colab notebook called "missing_values":

### drop columns with more than 50% nas

In [ ]:
df.shape

(91713, 184)

In [ ]:
df_new_col = df[df.columns[df.isnull().mean() < 0.5]]

print(f"We dropped {df.shape[1]-df_new_col.shape[1]} columns.")

We dropped 74 columns.


dropped 74 columns

### drop columns that are useless (ids), and correlated variables (bmi makes height and weight redundant)

In [ ]:
# Drop columns based on manual evaluation of data
final_df = df_new_col_row.drop(columns=['encounter_id', 'patient_id', 'icu_id', 'height', 'weight', 'readmission_status'], axis=1)
print("The shape of final_df after dropping columns is {}".format(final_df.shape))

The shape of final_df after dropping columns is (91605, 104)


### drop data with label 0 to have equal distribution of y

In [ ]:
alive_data = final_df[final_df['hospital_death'] == 0].reset_index(drop=True)
dead_data = final_df[final_df['hospital_death'] == 1].reset_index(drop=True)

In [ ]:
idx = list(range(0, len(alive_data)))
subset = sample(idx, len(dead_data))
alive_data = alive_data.loc[subset].reset_index(drop=True)

In [ ]:
# Appending the alive_data with the observations where hospital_death == 1
final_df = alive_data.append(dead_data)
final_df = final_df.sample(frac=1).reset_index(drop=True)

<ipython-input-13-f73533bd75b6>:2: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = alive_data.append(dead_data)


### Treating categorical features and numeric features differently

In [ ]:
def num_cat_col(df):
    '''
    Splits the columns of the dataframe into categorical and numerical columns
    and returns them as 2 separate lists.
    Columns having binary values (0 or 1) are added to the list of categorical columns.
    '''
    num_col = []
    cat_col = []
    new_dictionary = column_descriptions[column_descriptions['Data Type'] == 'binary']

    for column in df.columns:
        if df[column].dtypes == 'object':
            cat_col.append(column)
        elif column in [value for key, value in new_dictionary['Variable Name'].items()]:
            cat_col.append(column)
        else:
            num_col.append(column)
    return cat_col, num_col

cat_col, num_col = num_cat_col(final_df)

In [ ]:
df_cat = final_df[cat_col]
df_num = final_df[num_col]
print(f"There are {df_num.shape[1]} numeric features and {df_cat.shape[1]} categorical features")

There are 81 numeric features and 23 categorical features


In [ ]:
df_cat.isnull().sum()

hospital_death                    0
elective_surgery                  0
ethnicity                       240
gender                            9
hospital_admit_source          3503
icu_admit_source                 16
icu_stay_type                     0
icu_type                          0
apache_post_operative             0
arf_apache                      133
gcs_unable_apache               188
intubated_apache                133
ventilated_apache               133
aids                            133
cirrhosis                       133
diabetes_mellitus               133
hepatic_failure                 133
immunosuppression               133
leukemia                        133
lymphoma                        133
solid_tumor_with_metastasis     133
apache_3j_bodysystem            259
apache_2_bodysystem             259
dtype: int64

In [ ]:
binary_columns = column_descriptions[column_descriptions['Data Type'] == 'binary']['Variable Name']
binary_columns

3                   hospital_death
6                 elective_surgery
17              readmission_status
22           apache_post_operative
23                      arf_apache
30               gcs_unable_apache
35                intubated_apache
45               ventilated_apache
177                           aids
178                      cirrhosis
179              diabetes_mellitus
180                hepatic_failure
181              immunosuppression
182                       leukemia
183                       lymphoma
184    solid_tumor_with_metastasis
Name: Variable Name, dtype: object

### impute categorical and binary features

In [ ]:
def custom_imputer(column, binary_list):
    if column.name in binary_list:
        return column.fillna(-1) # nas in binary features will be imputed with -1
    else:
        return column.fillna("Unknown") # nas in categorical features will be imputed with "unknown"

df_cat_imputed = df_cat.apply(lambda column: custom_imputer(column, binary_columns))



In [ ]:
df_cat_imputed.isnull().sum()

hospital_death                 0
elective_surgery               0
ethnicity                      0
gender                         0
hospital_admit_source          0
icu_admit_source               0
icu_stay_type                  0
icu_type                       0
apache_post_operative          0
arf_apache                     0
gcs_unable_apache              0
intubated_apache               0
ventilated_apache              0
aids                           0
cirrhosis                      0
diabetes_mellitus              0
hepatic_failure                0
immunosuppression              0
leukemia                       0
lymphoma                       0
solid_tumor_with_metastasis    0
apache_3j_bodysystem           0
apache_2_bodysystem            0
dtype: int64

### Impute numeric features with KNN Imputer

In [ ]:
knn_imputer = KNNImputer(n_neighbors=3, weights='uniform')
df_num_imputed = knn_imputer.fit_transform(df_num)
df_num_imputed = pd.DataFrame(df_num_imputed, columns=df_num.columns)


In [ ]:
df_num_imputed.isnull().sum()

hospital_id           0
age                   0
bmi                   0
pre_icu_los_days      0
apache_2_diagnosis    0
                     ..
d1_potassium_min      0
d1_sodium_max         0
d1_sodium_min         0
d1_wbc_max            0
d1_wbc_min            0
Length: 81, dtype: int64

In [ ]:
final_df_clean = pd.concat([df_num_imputed, df_cat_imputed], axis=1)


In [ ]:
final_df_clean = pd.get_dummies(final_df_clean) # One hot encode

In [ ]:
final_df_clean.shape

(15792, 186)

In [ ]:
final_df_clean.to_csv('/content/drive/MyDrive/HW docs/מודלי חיזוי ברפואה/final_df_clean.csv', index=False)

# Chapter 5: Uncertainty Measures

## Imports

In [ ]:
from sklearn.utils import resample
from sklearn.metrics import roc_auc_score, recall_score, precision_score
from tqdm import tqdm
from sklearn.linear_model import LogisticRegression
from sklearn.pipeline import Pipeline
import plotly.graph_objects as go
from sklearn.metrics import confusion_matrix
from sklearn.metrics import roc_auc_score, recall_score, precision_score, confusion_matrix
from sklearn.utils import resample
from tqdm import tqdm
import numpy as np

## Functions

In [ ]:
model_name2num = {'KNN':2, 'LR':1, 'XGB': 3}

def plot_violin(model_name, kind='Basic'):
  """
  Creates a violin plot to visualize the distribution of performance metrics for a given model.

  Args:
      model_name (str): The name of the model to plot (must be present in the 'model_name2num' dictionary).
      kind (str, optional): The type of bootstrap used for the performance metrics. Defaults to 'Basic'.

  Explanation:
      * Maps model names to numerical values ('model_name2num' dictionary).
      * Iterates over performance metrics (AUC, Sensitivity, etc.).
      * Extracts metric values from the 'models' data structure.
      * Creates a violin plot for each metric using `go.Violin`.
      * Customizes the plot layout with titles and labels.
  """

  plot_data = []
  for metric in ['AUC', 'sensitivity', 'PPV', 'specificity', 'NPV']:
      metric_values = models[model_name2num[model_name]][1][metric]
      plot_data.append(go.Violin(y=metric_values, name=metric, box_visible=True, meanline_visible=True))

  fig = go.Figure(data=plot_data)

  fig.update_layout(
      title=f'Performance Metrics Distribution on {model_name} with {kind} Bootstrap',
      yaxis_title='Metric Values',
      xaxis_title='Metrics',
      showlegend=True
  )

  fig.show()

## Let's calculate AIC:

In [ ]:
# from sklearn.metrics import log_loss

# n = len(y_train)

# y_pred_proba_lr = best_ridge_model.predict_proba(X_train)
# nll_lr = log_loss(y_train, y_pred_proba_lr)
# k_lr = best_ridge_model.named_steps['logisticregression'].coef_.shape[1] + 1
# aic_lr = 2 * k_lr + 2 * nll_lr
# print('LR AIC:', aic_lr)

# y_pred_proba_GS = xgb_model_with_GS.predict_proba(X_train)
# nll_GS = log_loss(y_train, y_pred_proba_GS)
# k_GS = sum(tree.count('yes=') for tree in xgb_model_with_GS.get_booster().get_dump())
# aic_GS = 2 * k_GS + 2 * nll_GS
# print('XGB AIC:', aic_GS)

## Bootstrap

In [ ]:
data = df_imputed

# Untrained models
untrained_models = {
    1: Pipeline([
    ('scaler', StandardScaler()),
    ('logreg', LogisticRegression(C=0.01, solver='saga', verbose=0))
    ]) ,
    2: KNeighborsClassifier(n_neighbors=18, weights='distance'),
    3: xgb.XGBClassifier(
                                  max_depth=6,
                                  min_samples_split= 70,
                                  min_samples_leaf=50,
                                  criterion='gini',
                                  max_features= None,
                                  splitter='best',
                                  ccp_alpha=0.0,
                                  class_weight=None,
                                  max_leaf_nodes=None,
                                  min_impurity_decrease=0.0,
                                  min_weight_fraction_leaf=0.0,
                                  random_state=1
                              )
}

model_names = ['LR', 'KNN', 'XGB']
num_iterations = 100
models_count = len(untrained_models)

### Basic Bootstraping

In [ ]:
# Initialize the models dictionary
models = {model_num: (untrained_models[model_num], {'AUC': [], 'sensitivity': [],
                                                    'PPV': [], 'specificity': [], 'NPV': []})
          for model_num in range(1, models_count + 1)}

# Begin bootstrapping iterations
for _ in tqdm(range(num_iterations)):
  # Resample the training data with stratification
  X_train_resampled, y_train_resampled = resample(X_train, y_train, stratify=y_train)

  for model_num, (model, model_metrics) in models.items():

    model.fit(X_train_resampled, y_train_resampled)
    y_pred = model.predict(X_test)

    # If possible, get class probabilities (for calculating AUC)
    y_pred_proba = model.predict_proba(X_test)[:, 1] if hasattr(model, "predict_proba") else None

    # Calculate AUC if class probabilities are available
    if y_pred_proba is not None:
      model_metrics['AUC'].append(roc_auc_score(y_test, y_pred_proba))

    # Calculate confusion matrix and derived metrics
    tn, fp, fn, tp = confusion_matrix(y_test, y_pred).ravel()

    sensitivity = tp / (tp + fn)
    model_metrics['sensitivity'].append(sensitivity)

    precision = tp / (tp + fp)
    model_metrics['PPV'].append(precision)

    specificity = tn / (tn + fp)
    model_metrics['specificity'].append(specificity)

    npv = tn / (tn + fn) if (tn + fn) != 0 else None  # Avoid division by zero
    model_metrics['NPV'].append(npv)


100%|██████████| 100/100 [23:13<00:00, 13.93s/it]


In [ ]:
models_summary = []

for model_num, (model, model_metrics) in models.items():
    model_summary = {
      'Model': model_names[model_num-1],
      'AUC': f"{np.round(np.mean(model_metrics['AUC']), 3)}, {np.round(np.std(model_metrics['AUC']), 3)}, {np.round(np.percentile(model_metrics['AUC'], [2.5, 97.5]), 3).tolist()}",
      'Sensitivity': f"{np.round(np.mean(model_metrics['sensitivity']), 3)}, {np.round(np.std(model_metrics['sensitivity']), 3)}, {np.round(np.percentile(model_metrics['sensitivity'], [2.5, 97.5]), 3).tolist()}",
      'PPV': f"{np.round(np.mean(model_metrics['PPV']), 3)}, {np.round(np.std(model_metrics['PPV']), 3)}, {np.round(np.percentile(model_metrics['PPV'], [2.5, 97.5]), 3).tolist()}",
      'Specificity': f"{np.round(np.mean(model_metrics['specificity']), 3)}, {np.round(np.std(model_metrics['specificity']), 3)}, {np.round(np.percentile(model_metrics['specificity'], [2.5, 97.5]), 3).tolist()}",
      'NPV': f"{np.round(np.mean(model_metrics['NPV']), 3)}, {np.round(np.std(model_metrics['NPV']), 3)}, {np.round(np.percentile(model_metrics['NPV'], [2.5, 97.5]), 3).tolist()}",
    }

    models_summary.append(model_summary)

models_summary_df = pd.DataFrame(models_summary)

models_summary_df

Model                           AUC                   Sensitivity  \
0    LR  0.875, 0.002, [0.872, 0.878]  0.784, 0.005, [0.775, 0.793]   
1   KNN  0.771, 0.004, [0.764, 0.779]   0.598, 0.01, [0.579, 0.618]   
2   XGB  0.885, 0.003, [0.879, 0.889]   0.809, 0.006, [0.799, 0.82]   

                            PPV                   Specificity  \
0   0.802, 0.004, [0.794, 0.81]  0.799, 0.005, [0.789, 0.809]   
1  0.744, 0.008, [0.728, 0.759]   0.786, 0.01, [0.771, 0.804]   
2  0.806, 0.005, [0.796, 0.816]   0.798, 0.007, [0.786, 0.81]   

                            NPV  
0  0.781, 0.004, [0.774, 0.788]  
1  0.654, 0.005, [0.644, 0.665]  
2   0.801, 0.005, [0.793, 0.81]

In [ ]:
for model in ['KNN', 'LR', 'XGB']:
  plot_violin(model)

### 632 Bootstraping

In [ ]:
models = {model_num: (untrained_models[model_num], {'AUC': [], 'sensitivity': [], 'PPV': [], 'specificity': [], 'NPV': []})
          for model_num in range(1, models_count + 1)}

original_metrics = {}
for model_num, (model, _) in models.items():
    model.fit(X_train, y_train)
    y_pred = model.predict(X_test)
    y_pred_proba = model.predict_proba(X_test)[:, 1] if hasattr(model, "predict_proba") else None
    tn, fp, fn, tp = confusion_matrix(y_test, y_pred).ravel()

    # store original metrics on the test set
    original_auc = roc_auc_score(y_test, y_pred_proba) if y_pred_proba is not None else None
    original_sensitivity = recall_score(y_test, y_pred)
    original_precision = precision_score(y_test, y_pred)
    original_specificity = tn / (tn + fp)
    original_npv = tn / (tn + fn) if (tn + fn) != 0 else None

    original_metrics[model_num] = {'AUC': original_auc,
                                   'sensitivity': original_sensitivity,
                                   'PPV': original_precision,
                                   'specificity': original_specificity,
                                   'NPV': original_npv}

for _ in tqdm(range(num_iterations)):
    X_train_resampled, y_train_resampled = resample(X_train, y_train, stratify=y_train)

    for model_num, (model, model_metrics) in models.items():
        model.fit(X_train_resampled, y_train_resampled)
        y_pred = model.predict(X_test)
        y_pred_proba = model.predict_proba(X_test)[:, 1] if hasattr(model, "predict_proba") else None
        tn, fp, fn, tp = confusion_matrix(y_test, y_pred).ravel()

        boot_auc = roc_auc_score(y_test, y_pred_proba) if y_pred_proba is not None else None
        boot_sensitivity = recall_score(y_test, y_pred)
        boot_precision = precision_score(y_test, y_pred)
        boot_specificity = tn / (tn + fp)
        boot_npv = tn / (tn + fn) if (tn + fn) != 0 else None

        # Calculate weighted bootstrap metrics
        model_metrics['AUC'].append(0.632 * boot_auc + 0.368 * original_metrics[model_num]['AUC'] if boot_auc is not None else None)
        model_metrics['sensitivity'].append(0.632 * boot_sensitivity + 0.368 * original_metrics[model_num]['sensitivity'])
        model_metrics['PPV'].append(0.632 * boot_precision + 0.368 * original_metrics[model_num]['PPV'])
        model_metrics['specificity'].append(0.632 * boot_specificity + 0.368 * original_metrics[model_num]['specificity'])
        model_metrics['NPV'].append(0.632 * boot_npv + 0.368 * original_metrics[model_num]['NPV'])

100%|██████████| 100/100 [23:15<00:00, 13.95s/it]


In [ ]:
models_summary = []

for model_num, (model, model_metrics) in models.items():
    model_summary = {
        'Model': model_names[model_num-1],
        'AUC': f"{np.round(np.mean(model_metrics['AUC']), 3)}, {np.round(np.std(model_metrics['AUC']), 3)}, {np.round(np.percentile(model_metrics['AUC'], [2.5, 97.5]), 3).tolist()}",
        'Sensitivity': f"{np.round(np.mean(model_metrics['sensitivity']), 3)}, {np.round(np.std(model_metrics['sensitivity']), 3)}, {np.round(np.percentile(model_metrics['sensitivity'], [2.5, 97.5]), 3).tolist()}",
        'PPV': f"{np.round(np.mean(model_metrics['PPV']), 3)}, {np.round(np.std(model_metrics['PPV']), 3)}, {np.round(np.percentile(model_metrics['PPV'], [2.5, 97.5]), 3).tolist()}",
        'Specificity': f"{np.round(np.mean(model_metrics['specificity']), 3)}, {np.round(np.std(model_metrics['specificity']), 3)}, {np.round(np.percentile(model_metrics['specificity'], [2.5, 97.5]), 3).tolist()}",
        'NPV': f"{np.round(np.mean(model_metrics['NPV']), 3)}, {np.round(np.std(model_metrics['NPV']), 3)}, {np.round(np.percentile(model_metrics['NPV'], [2.5, 97.5]), 3).tolist()}",
    }

    models_summary.append(model_summary)

models_summary_df = pd.DataFrame(models_summary)

models_summary_df

Model                           AUC                   Sensitivity  \
0    LR  0.877, 0.001, [0.874, 0.879]  0.784, 0.003, [0.777, 0.791]   
1   KNN  0.778, 0.003, [0.773, 0.783]   0.599, 0.006, [0.588, 0.61]   
2   XGB  0.886, 0.002, [0.883, 0.889]   0.812, 0.004, [0.804, 0.82]   

                            PPV                   Specificity  \
0  0.802, 0.003, [0.798, 0.806]  0.799, 0.003, [0.793, 0.805]   
1  0.749, 0.005, [0.737, 0.758]  0.791, 0.006, [0.777, 0.803]   
2  0.807, 0.003, [0.801, 0.813]  0.799, 0.004, [0.791, 0.806]   

                            NPV  
0  0.781, 0.003, [0.776, 0.786]  
1  0.656, 0.003, [0.649, 0.661]  
2  0.804, 0.003, [0.798, 0.811]

In [ ]:
for model in ['KNN', 'LR', 'XGB']:
  plot_violin(model, kind = '.632')

## Interpretation

Dr. Smith, when we calculate the standard deviation (std), mean, and confidence interval (CI) on the metrics of the bootstrap, we're assessing the reliability of our model's predictions. The mean tells us the average performance of our model across different samples. The standard deviation gives us an idea of how much variability there is in our model's performance; a smaller std means our model's performance is consistent across samples. The confidence interval provides a range within which we are certain (usually 95% confident) the true performance metric lies, offering a measure of the precision of our estimate. Together, these measures help us understand the robustness and reliability of our predictions.

# Chapter 6: Fairness

## Imports

In [ ]:
import pandas as pd
from sklearn.metrics import roc_auc_score, recall_score, precision_score, f1_score
import plotly.graph_objects as go
import numpy as np
from sklearn.metrics import confusion_matrix
from itertools import combinations, product
from tqdm import tqdm
import warnings
warnings.filterwarnings("ignore")

## Funcitons

In [ ]:
def compare_performance_measures(X_test, y_test, model, subgroup_conds, model_name):
    """
    Function to compare all performance measures across subgroups for a single model.

    :param X_test: DataFrame containing the test features.
    :param y_test: Series containing the test labels.
    :param model: A single model to evaluate.
    :param subgroup_conds: List of conditions defining the subgroups.
    :return: None.
    """

    metrics_data = []
    metrics_types = ['AUC', 'Sensitivity', 'PPV', 'Specificity', 'NPV']

    # Iterate over each subgroup condition
    for cond, label in subgroup_conds.items():
        query_str = " and ".join(cond) if isinstance(cond, tuple) else cond
        sub_df = X_test.query(query_str)
        if sub_df.empty:
            continue
        true_labels = y_test.loc[sub_df.index]

        predictions = model.predict(sub_df)
        pred_proba = model.predict_proba(sub_df)[:, 1] if hasattr(model, "predict_proba") else None

        tn, fp, fn, tp = confusion_matrix(true_labels, predictions).ravel()


        # Calculate metrics
        metrics_data.append({
            'Subgroup': label,
            'Metric': 'AUC',
            'Value': roc_auc_score(true_labels, pred_proba) if hasattr(model, "predict_proba") and len(true_labels.value_counts()) > 1 else None

        })
        metrics_data.append({'Subgroup': label, 'Metric': 'Sensitivity', 'Value': tp / (tp + fn)})
        metrics_data.append({'Subgroup': label, 'Metric': 'PPV', 'Value': tp / (tp + fp)})
        metrics_data.append({'Subgroup': label, 'Metric': 'Specificity', 'Value': tn / (tn + fp)})
        metrics_data.append({'Subgroup': label, 'Metric': 'NPV', 'Value': tn / (tn + fn) if (tn + fn) != 0 else None})

    df_metrics = pd.DataFrame(metrics_data)

    # Plotting each metric for each subgroup using Plotly Express

    color_sequence = ['red', 'green', 'blue', 'orange', 'purple']
    fig = px.bar(df_metrics, x='Subgroup', y='Value', color='Metric', barmode='group', title=f"Performance Metrics by Subgroup with {model_name}", color_discrete_sequence=color_sequence)
    fig.update_xaxes(tickfont=dict(size=16))

    fig.update_layout(xaxis_title='Subgroup', yaxis_title='Metric Value')
    fig.show()


def model_comparison(model, model_name):
  print("Let's compare basic models")

  males_vs_females = {
    'age > 0' : 'All data',
    'gender_M == 1': 'Males',
    'gender_F == 1': 'Females',
  }
  compare_performance_measures(X_test, y_test, model, males_vs_females, model_name)

  age_subgroups = {
    'age > 0' : 'All data',
    'age < 30': 'Younger than 30',
    'age >= 30 and age < 40': 'Aged 30 to 39',
    'age >= 40 and age < 50': 'Aged 40 to 49',
    'age >= 50 and age < 60': 'Aged 50 to 59',
    'age >= 60 and age < 70': 'Aged 60 to 69',
    'age >= 70 and age < 80': 'Aged 70 to 79',
    'age >= 80': 'Aged 80 and older',
  }
  compare_performance_measures(X_test, y_test, xgb_model_with_GS, age_subgroups, model_name)

  ethnicity_subgroups = {
      'age > 0' : 'All data',
      'ethnicity_Caucasian == 1': 'Caucasian',
      '`ethnicity_Native American` == 1': 'Native American',
      '`ethnicity_Other/Unknown` == 1': 'Other/Unknown Ethnicity',
      '`ethnicity_African American` == 1': 'African American',
      'ethnicity_Asian == 1': 'Asian',
  }
  compare_performance_measures(X_test, y_test, xgb_model_with_GS, ethnicity_subgroups, model_name)

  basic_subgroups_dict = {
      'age > 0' : 'All data',
      '`hospital_id_30.0` == 1': 'Hospital #30 Patients',
      '`hospital_id_70.0` == 1': 'Hospital #70 Patients',
      '`hospital_id_100.0` == 1': 'Hospital #100 Patients',
      '`hospital_id_118.0` == 1': 'Hospital #118 Patients',
  }
  compare_performance_measures(X_test, y_test, xgb_model_with_GS, basic_subgroups_dict, model_name)

  print("Let's go deeper")

  intersecting_2_subgroups_dict = {
    'age > 0' : 'All data',
    ('age >= 80', 'gender_F == 1'): 'Females Aged 80 and older',
    ('ethnicity_Caucasian == 1', 'gender_M == 1'): 'Caucasian Males',
    ('ethnicity_Asian == 1', 'gender_F == 1'): 'Asian Females',
    ('`hospital_id_19.0` == 1', '`ethnicity_African American` == 1'): 'Hospital #19 African American Patients',
    ('gender_F == 1', 'ethnicity_Caucasian == 1'): 'Caucasian Females',
    ('`hospital_id_188.0` == 1', 'gender_F == 1'): 'Hospital #188 Female Patients',
  }

  compare_performance_measures(X_test, y_test, xgb_model_with_GS, intersecting_2_subgroups_dict, model_name)

  print("Even deeper")
  intersecting_3_subgroups_dict = {
    'age > 0' : 'All data',
    ('gender_M == 1', 'age < 30', '`hospital_id_30.0` == 1'): 'Young Males at Hospital #30',
    ('gender_F == 1', 'ethnicity_Caucasian == 1', '`hospital_id_70.0` == 1'): 'Caucasian Females at Hospital #70',
    ('age >= 80', '`ethnicity_Native American` == 1', '`hospital_id_100.0` == 1'): 'Native American Aged 80+ at Hospital #100',
    ('gender_F == 1', '`ethnicity_African American` == 1', 'age >= 50 and age < 60'): 'African American Females Aged 50 to 59',
    ('gender_M == 1', 'age >= 70 and age < 80', '`hospital_id_70.0` == 1'): 'Males Aged 70 to 79 at Hospital #70',
    ('ethnicity_Caucasian == 1', 'age >= 80', '`hospital_id_118.0` == 1'): 'Caucasian Aged 80+ at Hospital #118',
    ('age >= 60 and age < 70', '`ethnicity_Other/Unknown` == 1', '`hospital_id_70.0` == 1'): 'Unknown Ethnicity Aged 60 to 69 at Hospital #70',
    ('gender_F == 1', 'age >= 70', '`ethnicity_Caucasian` == 1'): 'Caucasian Females Aged 70+',
    ('age >= 80', 'gender_F == 1', '`hospital_id_118.0` == 1'): 'Females Aged 80+ at Hospital #118',
  }

  compare_performance_measures(X_test, y_test, xgb_model_with_GS, intersecting_3_subgroups_dict, model_name)

  intersecting_4_subgroups_dict = {
    'age > 0' : 'All data',
    ('age >= 20 and age < 40', 'gender_M == 1', '`hospital_id_118.0` == 1', 'ethnicity_Caucasian == 1'): "Caucasian Males Aged 20 to 39 at Hospital #118",
    ('age >= 60 and age < 70', 'gender_M == 1', '`hospital_id_118.0` == 0 and `hospital_id_19.0` == 0 and `hospital_id_188.0` == 0', '`ethnicity_Other/Unknown` == 1'): "Other/Unknown Ethnicity Males, 60-69, Outside Top 3 Hospitals",
    ('age >= 50 and age < 60', 'gender_F == 1', '`hospital_id_118.0` == 1', '`ethnicity_African American` == 1'): "African American Females Aged 50 to 59 at Hospital #161",
    ('age >= 20 and age < 50', 'gender_F == 1', '`hospital_id_19.0` == 1', 'ethnicity_Caucasian == 1'): "Caucasian Females Aged 20 to 49 at Hospital #19",
  }

  compare_performance_measures(X_test, y_test, xgb_model_with_GS, intersecting_4_subgroups_dict, model_name)


def generate_subgroups(query_lists):
    """
    Generates all possible subgroups (tuples) formed by combining elements from the input lists.

    Args:
        query_lists (list of lists): A list of lists, where each sublist represents a set of elements to combine.

    Returns:
        list: A list of tuples, where each tuple represents a subgroup formed by combining elements across the input lists.
    """
    subgroups = []
    for list1, list2 in combinations(query_lists, 2):
        subgroups.extend(product(list1, list2))
    for list1, list2, list3 in combinations(query_lists, 3):
        subgroups.extend(product(list1, list2, list3))
    for list1, list2, list3, list4 in combinations(query_lists, 4):
        subgroups.extend(product(list1, list2, list3, list4))
    return subgroups


def find_empty_subgroups(subpopulation_queries, X):
  """
    Identifies subgroups within a dataset that have no corresponding data points (i.e., empty subgroups).

    Args:
        subpopulation_queries (list): A list of queries defining the subgroups. Each query can be a tuple of conditions or a single condition string.
        X (pandas.DataFrame): The DataFrame containing the data to be analyzed.

    Returns:
        list: A list of queries that resulted in empty subgroups.
  """
  empty_queries = []
  for query in subpopulation_queries:
    S = X.query(" and ".join(query) if isinstance(query, tuple) else query).index

    if len(S) == 0:
      empty_queries.append(query)

  return empty_queries


def calc_calibration_itl(model, X, y, subgroup_queries):
  """
    Calculates the calibration-in-the-large (ITL) for each subgroup defined by the provided queries.

    Calibration-in-the-large measures how well the average predicted probability for a subgroup
    matches the observed event rate within that subgroup.

    Args:
        model: A fitted model with a `predict_proba` method.
        X (pandas.DataFrame): The feature DataFrame.
        y (pandas.Series): The target variable.
        subgroup_queries (list): A list of queries defining the subgroups. Each query can be
                                 a tuple of conditions or a single condition string.

    Returns:
        list:  A list of calibration-in-the-large values (floats), one for each subgroup query.
  """

  y = pd.Series(y, index=X.index)
  p = pd.Series(model.predict_proba(X)[:, 1], index=X.index)

  calibrations_list = []

  for query in subgroup_queries:
    S = X.query(" and ".join(query) if isinstance(query, tuple) else query).index
    avg_predicted_proba = np.mean(p[S])
    overall_event_rate = np.mean(y[S])
    calibration_intercept = avg_predicted_proba - overall_event_rate
    calibrations_list.append(calibration_intercept)

  return calibrations_list


def test_mc_across_models(model, sorted_queries, y_test, model_name):
  """
  Evaluates the calibration-in-the-large (ITL) of a model across subgroups, both before and after calibration. Plots the results for comparison.

  Args:
      model: The fitted model to evaluate.
      sorted_queries: A list of queries defining the subgroups, sorted by subgroup size.
      y_test: The true labels (target values) for the test set.
      model_name (str): The name of the model for the plot title.

  Returns:
      tuple:
         - The calibrated model object (ClibratedPredictor)
         - The original ITL calibration values
         - The ITL calibration values after calibration
  """
  calibrated_model = ClibratedPredictor(model, sorted_queries, y_test)
  calibrations_list = calc_calibration_itl(model, X_test, y_test, sorted_queries) # 1.5 min. to run
  calibrated_calibrations_list = calc_calibration_itl(calibrated_model, X_test, y_test, sorted_queries)

  data = {
    'Original': calibrations_list,
    'Calibrated': calibrated_calibrations_list,
    'Index': range(len(calibrations_list))
  }

  df = pd.DataFrame(data)

  # Melt the DataFrame so that it's in a tidy format Plotly can use to automatically generate a legend
  df_melted = df.melt(id_vars=['Index'], value_vars=['Original', 'Calibrated'],
                      var_name='Type', value_name='Value')

  # Plot using the melted DataFrame
  fig = px.line(df_melted,
                x='Index',
                y='Value',
                color='Type', # This will automatically create a legend based on the 'Type' column
                title=f'Calibration in The Large Across Subgroups ({model_name} model)')

  fig.update_layout(
      xaxis_title="Subgroup Index (Widest to Narrowest)",
      yaxis_title="Calibration in The Large"
  )

  fig.show()

  return calibrated_model, calibrations_list, calibrated_calibrations_list


def plot_calibrated_metrics(model_name):
  """
  Calculates and plots performance metrics for a calibrated model.

  Args:
      model_name (str): The name of the model to retrieve from the 'calibrated_dict'.

  Explanation:
      1. Retrieves the calibrated model and predictions from the 'calibrated_dict'.
      2. Calculates performance metrics (AUC, Sensitivity, PPV, Specificity, NPV).
      3. Creates a DataFrame to store the calculated metric values.
      4. Generates a bar chart using Plotly to visualize the performance metrics.
  """

  predictions = calibrated_dict[model_name]['calibrated-model'].predict(X_test)
  probas = calibrated_dict[model_name]['calibrated-model'].proba[:,1]
  metrics = ['Sensitivity', 'PPV', 'Specificity', 'NPV']

  metrics_dict = {k: None for k in metrics}

  tn, fp, fn, tp = confusion_matrix(y_test, predictions).ravel()

  metrics_dict['AUC'] = roc_auc_score(y_test, probas)
  metrics_dict['Sensitivity'] = tp / (tp + fn)
  metrics_dict['PPV'] = tp / (tp + fp)
  metrics_dict['Specificity'] = tn / (tn + fp)
  metrics_dict['NPV'] = tn / (tn + fn) if (tn + fn) != 0 else None

  metrics_df = pd.DataFrame.from_dict(metrics_dict, orient='index', columns=['Value'])
  metrics_df.reset_index(inplace=True)
  metrics_df.rename(columns={'index': 'Metric'}, inplace=True)

  fig = px.bar(metrics_df, x='Metric', y='Value', title=f'Model Calibrated Performance Metrics on {model_name}')

  fig.update_layout(
      xaxis_title=None,
      yaxis_title="Metric Value",
  )

  fig.show()


def plot_regular_metrics(model_name):
  """
    Calculates and plots performance metrics for the original (uncalibrated) model.

    Args:
        model_name (str): The name of the model to retrieve from the 'calibrated_dict'.

    Differences from 'plot_calibrated_metrics':
        *  Retrieves the original, uncalibrated model from 'calibrated_dict'.
        *  The title indicates that these are performance metrics for the original model.

    Explanation:
        1. Retrieves the original model and predictions from the 'calibrated_dict'.
        2. Calculates performance metrics (AUC, Sensitivity, PPV, Specificity, NPV).
        3. Creates a DataFrame to store the calculated metric values.
        4. Generates a bar chart using Plotly to visualize the performance metrics.
  """
  predictions = calibrated_dict[model_name]['model'].predict(X_test)
  probas = calibrated_dict[model_name]['model'].predict_proba(X_test)[:,1]
  metrics = ['Sensitivity', 'PPV', 'Specificity', 'NPV']

  metrics_dict = {k: None for k in metrics}

  tn, fp, fn, tp = confusion_matrix(y_test, predictions).ravel()

  metrics_dict['AUC'] = roc_auc_score(y_test, probas)
  metrics_dict['Sensitivity'] = tp / (tp + fn)
  metrics_dict['PPV'] = tp / (tp + fp)
  metrics_dict['Specificity'] = tn / (tn + fp)
  metrics_dict['NPV'] = tn / (tn + fn) if (tn + fn) != 0 else None

  metrics_df = pd.DataFrame.from_dict(metrics_dict, orient='index', columns=['Value'])
  metrics_df.reset_index(inplace=True)
  metrics_df.rename(columns={'index': 'Metric'}, inplace=True)

  fig = px.bar(metrics_df, x='Metric', y='Value', title=f'Model Performance Metrics on {model_name}')
  fig.update_traces(marker_color='#960b0b')  # Your desired color

  fig.update_layout(
      xaxis_title=None,
      yaxis_title="Metric Value",
  )

  fig.show()


def plot_distribution(model_name):
  """
    Visualizes the distribution of calibration-in-the-large (ITL) values before and after applying a multi-calibration process.

    Args:
        model_name (str): The name of the model to retrieve data from the 'calibrated_dict'.

    Explanation:
        1. Retrieves calibration-in-the-large values (both before and after calibration) from the 'calibrated_dict'.
        2. Creates a DataFrame to organize the calibration data.
        3. Generates an overlaid histogram using Plotly to compare the distributions.
        4. Sets the y-axis to a logarithmic scale for better visualization of distributions.
  """
  vector1 = calibrated_dict[model_name]['calibrations_list']
  vector2 = calibrated_dict[model_name]['calibrated-calibrations-list']
  df = pd.DataFrame({'Data 1': vector1, 'Data 2': vector2})
  fig = px.histogram(df, x=df.columns, barmode='overlay', opacity=0.6,
                   title=f'Distribution of Calibration on {model_name} Before and After Multi-Calibration')

  fig.update_layout(bargap=0.1, yaxis_type='log')  # Set y-axis to log scale

  fig.show()

**General Considerations:**

*Protected Variables:*
- Age: Different age groups may have different baseline mortality rates, and the model should not disproportionately predict higher mortality for certain age groups.
- Gender: Gender should not influence the predictions unfairly. For example, the model should not predict higher mortality for one gender over the other if there's no medical justification.
- Ethnicity: Similarly, ethnicity should not lead to biased predictions. It's important to ensure that the model does not unfairly disadvantage certain ethnic groups.
- Hospital: The hospital where the patient was admitted might serve as a proxy for socioeconomic status (SES). It's crucial to avoid predictions that are biased based on the hospital.

*Performance Measures in Various Subgroups:*
- It's essential to evaluate the model's performance metrics (such as accuracy, sensitivity, specificity, etc.) across different subgroups defined by the protected variables.
- For example, performance should be assessed separately for different age groups, genders, ethnicities, and hospitals. Additionally, performance should be evaluated for intersecting variables (e.g., elderly females of a specific ethnicity admitted to a particular hospital).

## Lets visualize the protected variables Dr. Smith asked us to focus on:

In [ ]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import pandas as pd

# Prepare the data
hospital_id_counts = best_df['hospital_id'].value_counts()
gender_counts = best_df['gender'].value_counts()
ethnicity_counts = best_df['ethnicity'].value_counts()
age_data = best_df['age']

# Create a subplot figure with 2 rows and 3 columns
# The first plot spans all columns in the first row
fig = make_subplots(
    rows=2, cols=3,
    specs=[[{"colspan": 3, "type": "bar"}, None, None], [{"type": "bar"}, {"type": "bar"}, {"type": "histogram"}]],
    subplot_titles=("Hospital ID Distribution", "Gender Distribution", "Ethnicity Distribution", "Age Distribution"),
    vertical_spacing=0.2  # Increased from 0.1 to 0.2 for more space between rows
)

# Add the plots
fig.add_trace(go.Bar(x=hospital_id_counts.index, y=hospital_id_counts.values, marker_color='blue'), row=1, col=1)
fig.add_trace(go.Bar(x=gender_counts.index, y=gender_counts.values, marker_color='green'), row=2, col=1)
fig.add_trace(go.Bar(x=ethnicity_counts.index, y=ethnicity_counts.values, marker_color='orange'), row=2, col=2)
fig.add_trace(go.Histogram(x=age_data, nbinsx=20, marker_color='red'), row=2, col=3)  # Adjust bins with nbinsx as needed

# Update layout for a better view
fig.update_layout(showlegend=False, height=600, width=1340)
fig.update_xaxes(title_text="Hospital ID", row=1, col=1)
fig.update_xaxes(title_text="Gender", row=2, col=1)
fig.update_xaxes(title_text="Ethnicity", row=2, col=2)
fig.update_xaxes(title_text="Age", row=2, col=3)
fig.update_yaxes(title_text="Count", row=1, col=1)
fig.update_yaxes(title_text="Count", row=2, col=1)
fig.update_yaxes(title_text="Count", row=2, col=2)
fig.update_yaxes(title_text="Count", row=2, col=3)

# Show the figure
fig.show()

In [ ]:
# Get a sense of the top hospitals by number of patients
best_df['hospital_id'].value_counts()

118    4333
19     3925
188    3095
161    2792
70     2754
       ... 
23        7
4         7
93        6
95        6
130       2
Name: hospital_id, Length: 147, dtype: int64

## Lets Compare Metrics

### KNN Comparison

In [ ]:
model_comparison(knn, 'KNN')

Let's compare basic models


Let's go deeper


Even deeper


### LR Comparison

In [ ]:
model_comparison(best_lasso_model, 'LR')

Let's compare basic models


Let's go deeper


Even deeper


### XGB Comparison

In [ ]:
model_comparison(xgb_model_with_GS, 'XGB')

Let's compare basic models


Let's go deeper


Even deeper


Dr. Smith, based in the plots a above - it is clear that there is an issue with fairness across protected features. we will consider implementing fairness-aware techniques focusing on equalizing acceptance rates, error rates, and ensuring calibration across subgroups. This involves adjusting training data or model outputs to mitigate biases against protected groups such as those defined by age, gender, ethnicity, and hospital admission. Multi-calibration could be particularly effective, aiming for accurate predictions across all possible intersections of subgroups, though it requires careful consideration to avoid compromising the performance for certain groups. Continuous monitoring and adjustment based on subgroup performance are crucial to maintaining fairness over time.

## Dealing with Unfairness

In this case, we want to take the approach of Utilitarianism, which states that the overall gain in well-being should be considered. Hence, improving the acceptance or error rate of the small, potentially discriminated subgroup at the expense of the majority of the patients is not worth it. Moreover, equalizing acceptance rates means dropping these protected variables. This is not beneficial in medicine because gender, race, and age are crucial biological features that the models can learn from, and the hospital ID can give us a hint about the socioeconomic status of the patient, which can be proxies for hospital quality and the ability to afford more expensive treatments, which might affect the probability of mortality. On the other hand, equalizing error rates may entail compromises on the performance for some groups, making it comparable to the subgroups with the worst performance, and this is not fair as well.

As we learned in the lecture, multi-calibration offers the best trade-off of improving weak groups while not hurting the strong group's performance. So, we will implement it and see if it helps.

> We are basing our code on the pseudo-code provided in the lecture from: https://arxiv.org/abs/1711.08513

## Multi-calibration algorithm

### Lets find all of the valid subgroups

In [ ]:
gender_queries = ['gender_M == 1', 'gender_F == 1',]
age_queries = [f'age >= {a} and age < {a+10}' for a in range(10, 90, 10)]
ethnicity_queries = [f'`ethnicity_{e}` == 1' for e in ['Caucasian', 'Native American', 'Other/Unknown', 'African American', 'Asian']]
hospital_queries = [f'`hospital_id_{i}.0` == 1' for i in set(best_df['hospital_id'].value_counts().keys()) - {4, 34, 38, 74, 84, 93, 95, 129, 167, 198,}]

all_query_lists = [gender_queries, age_queries, ethnicity_queries, hospital_queries]
all_subgroups = generate_subgroups(all_query_lists)

subpopulation_queries = [
  *gender_queries,
  *age_queries,
  *ethnicity_queries,
  *hospital_queries,
  *all_subgroups
]

# comparison with the manual combination calculation
assert len(all_subgroups) == 2*8*5*137 + 8*5*137 + 2*5*137 + 2*8*137 + 2*8*5 + 2*8 + 2*5 + 2*137 + 8*5 + 8*137 + 5*137
print(f'Total subgroups = {len(subpopulation_queries)}')

empty_subgroups = find_empty_subgroups(subpopulation_queries, X_test) # 6 minutes to run (pickled for later use)
final_subgroup_queries = set(subpopulation_queries) - set(empty_subgroups)
len(final_subgroup_queries)

sorted_queries = sorted(final_subgroup_queries, key=lambda x: 0 if isinstance(x, str) else len(x))
print(f'Valid subgroups = {len(sorted_queries)}')

Total subgroups = 22355


### Lets build the CalibratedPredictor class, which will help us build up on the sklearn functionality

In [ ]:
class ClibratedPredictor:
  def __init__(self, model, subgroups, y_test):
    self.model = model
    self.subgroups = subgroups
    self.y_test = y_test
    self.proba = None

  def predict(self, X, y=None):
    if self.proba is None:
      self.predict_proba(X, y)

    p = self.proba[:, 1]
    preds = np.where(p >= 0.2, 1, 0)

    return preds

  def predict_proba(self, X, y=None):
    return self.multi_calibrate_predictor(X, y, self.subgroups)

  def multi_calibrate_predictor(self, X, y, subpopulation_queries, alpha=1e-3, max_iter=1):
    """
      Perform multi-calibration to ensure fairness across subgroups.

      :param predictor: A trained classifier with a predict_proba method.
      :param X: DataFrame containing the input features.
      :param y: Series containing the true labels.
      :param subpopulation_queries: List of strings representing the query to define each subgroup.
      :param alpha: The violation parameter.
      :param max_iter: Maximum number of iterations for the calibration process.
      :return: Calibrated probabilities.
    """

    y = pd.Series(self.y_test, index=X.index)
    p = self.model.predict_proba(X)[:, 1]
    calibrated_p = pd.Series(p.copy(), index=X.index)
    done = False

    for _ in range(max_iter):
      done = True
      for query in subpopulation_queries:
        S = X.query(" and ".join(query) if isinstance(query, tuple) else query).index

        delta_S = (y.loc[S] - calibrated_p.loc[S]).mean()
        if abs(delta_S) > alpha:
          calibrated_p.loc[S] += delta_S
          done = False

      if done: print("calibrated"); break

    calibrated_p[calibrated_p < 0] = 0
    calibrated_p[calibrated_p > 1] = 1

    calibrated_p = calibrated_p.values  # Not P-values XD
    zero_class = 1 - calibrated_p
    calibrated_p = np.concatenate([zero_class[:,np.newaxis], calibrated_p[:,np.newaxis]], axis=1)

    self.proba = calibrated_p

    return calibrated_p

### Lets test the multi calibration algorithm across models.

In [ ]:
calibrated_dict = {
    'KNN': {'model': knn},
    'LR': {'model': best_lasso_model},
    'XGB': {'model': xgb_model_with_GS}
}

for model_name, model_dict in calibrated_dict.items():
  model_dict['calibrated-model'], model_dict['calibrations_list'], model_dict['calibrated-calibrations-list'] = \
  test_mc_across_models(model_dict['model'], sorted_queries, y_test, model_name)

In [ ]:
# Calculate standard deviations and improvements
print("Standard Deviations of Calibrated Values:")
for model_name, data in calibrated_dict.items():
    original_std_dev = np.std(data['calibrations_list'])
    calibrated_std_dev = np.std(data['calibrated-calibrations-list'])

    print(f"\t- {model_name}: Original STD:{original_std_dev:.4f}; \
    Calibrated STD: {calibrated_std_dev:.4f} ({((original_std_dev/calibrated_std_dev)*100):.0f}% Improvement)")

Standard Deviations of Calibrated Values:
	- KNN: Original STD:0.3166;     Calibrated STD: 0.0278 (1140% Improvement)
	- LR: Original STD:0.2719;     Calibrated STD: 0.0282 (965% Improvement)
	- XGB: Original STD:0.2704;     Calibrated STD: 0.0355 (761% Improvement)


### Lets test the calibrated models on the whole test set and compare to the original models

In [ ]:
for model in ['KNN', 'LR', 'XGB']:
  plot_calibrated_metrics(model)

In [ ]:
for model in ['KNN', 'LR', 'XGB']:
  plot_regular_metrics(model)

### Lets see the improvement in the distribution

In [ ]:
for model in ['KNN', 'LR', 'XGB']:
  plot_distribution(model)